# Import Statements

In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import folium
from folium import plugins
from folium.plugins import HeatMap
from datetime import datetime
from datetime import timedelta
import math
import random
import timeit
import urllib.request, json # we will need urllib to communicate with the api and then json to read the data we get

---

# Bycicle Stations

## Retrieving bicycle stations in Duisburg

We simply send the API the request parameter city with the corresponding city ids.  
City IDs can be found here https://api.nextbike.net/maps/nextbike-live.json?list_cities=1

In [4]:
city_ids = ['129', '130', '131', '132', '133', '134', '135', '136', '137', '138'] # corresponding to all metropolradruhr cities
with urllib.request.urlopen("https://api.nextbike.net/maps/nextbike-live.json?city={}"
                            .format(','.join(city_ids))) as url:
    duisburg_stations_data = json.loads(url.read().decode())
    

Now we will go through the data, which is internally now stored as dictionary.  
We will save all stations data in a list called duisburg_stations.  
We also delete some key/value pairs, because they store lists, which will we cannot display in a dataframe.  
Notice that we only use stations, which have 'spot' set to true.  
As stated in nextbikes API documentation this means that this data is indeed a stations.  
Places with 'spot' set to false, are locations where people left their bike unauthorised.  

In [5]:
duisburg_stations = []
for city in duisburg_stations_data['countries'][0]['cities']:
    for place in city['places']:
        if place['spot'] == True:
            duisburg_stations.append({
                'id': place['number'],
                'name': place['name'],
                'lat': place['lat'],
                'lon': place['lng'],
                'city': city['alias']
            })

In [6]:
duisburg_stations = pd.DataFrame(duisburg_stations)
duisburg_stations['coordinates'] = list(zip(duisburg_stations['lat'].round(4), duisburg_stations['lon'].round(4)))
duisburg_stations.set_index('id', inplace=True)
duisburg_stations.drop(['lat', 'lon'], axis=1, inplace=True)
duisburg = pd.read_pickle('../0_data/duisburg_clean.pkl')
duisburg_stations['city'].unique()

array(['dortmund', 'bochum', 'bottrop', 'duisburg', 'essen',
       'gelsenkirchen', 'hamm', 'herne', 'muelheim', 'oberhausen'],
      dtype=object)

In [13]:
Du_map = folium.Map(location=(51.44, 6.83), zoom_start=10, control_scale=True, max_zoom=20)
Du_map.add_child(plugins.HeatMap(duisburg["dest"], radius=15)) #adding heatmap points with the cleaned orig coordinates

for index, row in duisburg_stations.iterrows():
    folium.CircleMarker(radius=5, location=row.coordinates, color='black', fill_color='black', popup=row['name'] + ' (' + row['city']+')').add_to(Du_map)
Du_map #showing Map

In [14]:
duisburg_stations.to_pickle('../0_data/stations/duisburg_stations.pkl')
duisburg_stations

name        city        coordinates
id                                                                
7302   Wittener Str. / Wilhelmplatz    dortmund  (51.5129, 7.4233)
7303       Hauptbahnhof Nordausgang    dortmund   (51.519, 7.4591)
7304                       Cinestar    dortmund  (51.5193, 7.4601)
7306  Hauptbahnhof/Bahnhofsvorplatz    dortmund  (51.5172, 7.4599)
7307                      RWE Tower    dortmund  (51.5167, 7.4618)
...                             ...         ...                ...
7018              Buschhausen Mitte  oberhausen   (51.503, 6.8325)
7019              Marina / Sea Life  oberhausen  (51.4935, 6.8808)
7020               Styrum Josefstr.  oberhausen  (51.4615, 6.8519)
7021              Alsfeld Jägerstr.  oberhausen  (51.5282, 6.8324)
7726                 Essener Straße  oberhausen  (51.4875, 6.8702)

[365 rows x 3 columns]

## Retrieving bicycle stations in Marburg

In [15]:
with urllib.request.urlopen("https://api.nextbike.net/maps/nextbike-live.json?city=438") as url:
    marburg_stations_data = json.loads(url.read().decode())

In [16]:
marburg_stations = []
for place in marburg_stations_data['countries'][0]['cities'][0]['places']:
    if place['spot'] == True:
            marburg_stations.append({
                'id': place['number'],
                'name': place['name'],
                'lat': place['lat'],
                'lon': place['lng']
            })

In [17]:
marburg_stations = pd.DataFrame(marburg_stations)
marburg_stations['coordinates'] = list(zip(marburg_stations['lat'].round(4), marburg_stations['lon'].round(4)))

In [18]:
marburg = pd.read_pickle('../0_data/marburg_clean.pkl')

In [19]:
Ma_map = folium.Map(location=(50.81, 8.74), zoom_start=10, control_scale=True, max_zoom=20)
Ma_map.add_child(plugins.HeatMap(marburg["orig"], radius=15)) #adding heatmap points with the cleaned orig coordinates

for index, row in marburg_stations.iterrows():
    folium.CircleMarker(radius=5, location=row.coordinates, color='black', fill_color='black', popup=row['name']).add_to(Ma_map)
    
    
Ma_map

In [20]:
# we drop all columns except for coordinates and number
# number is nextbikes internal id of a station, so we will use it as index
marburg_stations.drop(marburg_stations.columns.difference(['coordinates', 'id', 'name']), 1, inplace=True)
marburg_stations.set_index('id', inplace=True)

In [21]:
marburg_stations.to_pickle('../0_data/stations/marburg_stations.pkl')
marburg_stations.head(5)

name        coordinates
id                                                        
5150   Alte Kasseler Straße/Jägertunnel  (50.8229, 8.7747)
5151       Am Krekel/Stadtwerke Marburg  (50.7895, 8.7564)
5152  Am Plan/Wirtschaftswissenschaften   (50.8079, 8.767)
5153               An den Siechengärten  (50.8058, 8.7828)
5154         Cappel August-Bebel-Platz    (50.7784, 8.768)